In [1]:
import pandas as pd
import json
import os
import json
import re
import itertools

In [2]:
temp = [1]
temp[0:0]

[]

In [3]:
def read_dataset(filepath):
    with open(filepath) as file:
        data = json.load(file)
    file.close()
    return data

In [4]:
dwie_train = read_dataset('../data/datasets/dwie_before_preproc/dwirex_train.json')
dwie_test = read_dataset('../data/datasets/dwie_before_preproc/dwirex_test.json')
new_dwie = read_dataset('../data/datasets/dwie_before_preproc/new_dwie.json')
types = read_dataset('../data/datasets/dwie_before_preproc/types.json')

In [5]:
full_list = []
type_rel = types['relations']
for i in range(len(dwie_train[0])):
    
    ent_data = new_dwie['dataset']['train'][i]['entities']
    cluster_data = new_dwie['dataset']['train'][i]['clusters']
    rel_data = new_dwie['dataset']['train'][i]['relations']
    title = new_dwie['dataset']['train'][i]['doc_id']
    sent_span = new_dwie['dataset']['train'][i]['sentences_spans']
    words = new_dwie['dataset']['train'][i]['words']
    
    #Create sentences
    sent_list = []
    for pair in sent_span:
        start_pair = pair[0]
        end_pair = pair[1]
        sent = words[start_pair:end_pair]
        sent_list.append(sent)
    
    cluster_dict = {}
    for mini_dict in ent_data:
        cluster_no = mini_dict['cluster']
        if cluster_no not in cluster_dict.keys():
            cluster_dict[cluster_no] = []
        ent_type = cluster_data[cluster_no]['labels']
        if len(ent_type)>0:
            ent_type = [e for e in ent_type if e not in ['entity','none', 'other', 'misc','value']]
            ent_type = ent_type[-1] if len(ent_type)>0 else 'misc'
        else:
            ent_type = 'misc'
        sentence_minus = sent_list[0:mini_dict['sent_id']]
        token_minus = list(itertools.chain(*sentence_minus))
        len_tok_minus = len(token_minus)
        start_tok = mini_dict['start']-len_tok_minus
        end_tok = mini_dict['end']-len_tok_minus
        if start_tok<0:
            print(mini_dict['text'])
        cluster_dict[cluster_no].append({'name': mini_dict['text'],
                                        'pos': [start_tok,end_tok],
                                        'sent_id': mini_dict['sent_id'],
                                        'type': ent_type})
    #Create vertexset
    vertex_set_list = []
    clus_no_to_index = {}
    for j,key in enumerate(sorted(cluster_dict.keys())):
        clus_no_to_index[key] = j
        vertex_set_list.append(cluster_dict[key])
    
    #create labels (problem: labels inconsistent)
    rel_list = []
    for mini_rel_dict in rel_data:
        rel_dict = {}
        r = mini_rel_dict['p']
        h = mini_rel_dict['s']
        t = mini_rel_dict['o']
        try:
            rel_dict['r'] = r
            rel_dict['h'] = clus_no_to_index[h]
            rel_dict['t'] = clus_no_to_index[t]
            rel_dict['evidence'] = [0]
        except:
            continue
        rel_list.append(rel_dict)
    
    doc_dict = {}
    doc_dict['vertexSet'] = vertex_set_list
    doc_dict['labels'] = rel_list
    doc_dict['title'] = title
    doc_dict['sents'] = sent_list
    if doc_dict['vertexSet']==[]:
        continue
    if doc_dict['labels']==[]:
        continue
    full_list.append(doc_dict)

train_output = full_list
with open('../data/datasets/dwie_before_preproc/train_joint.json', 'w') as outfile:
    json.dump(train_output, outfile)

In [6]:
full_list = []
type_rel = types['relations']
for i in range(len(dwie_test[0])):
    
    ent_data = new_dwie['dataset']['test'][i]['entities']
    cluster_data = new_dwie['dataset']['test'][i]['clusters']
    rel_data = new_dwie['dataset']['test'][i]['relations']
    title = new_dwie['dataset']['test'][i]['doc_id']
    sent_span = new_dwie['dataset']['test'][i]['sentences_spans']
    words = new_dwie['dataset']['test'][i]['words']
    
    #Create sentences
    sent_list = []
    for pair in sent_span:
        start_pair = pair[0]
        end_pair = pair[1]
        sent = words[start_pair:end_pair]
        sent_list.append(sent)
    
    cluster_dict = {}
    for mini_dict in ent_data:
        cluster_no = mini_dict['cluster']
        if cluster_no not in cluster_dict.keys():
            cluster_dict[cluster_no] = []
        ent_type = cluster_data[cluster_no]['labels']
        if len(ent_type)>0:
            ent_type = [e for e in ent_type if e not in ['entity','none', 'other', 'misc','value']]
            ent_type = ent_type[-1] if len(ent_type)>0 else 'misc'
        else:
            ent_type = 'misc'
        sentence_minus = sent_list[0:mini_dict['sent_id']]
        token_minus = list(itertools.chain(*sentence_minus))
        len_tok_minus = len(token_minus)
        start_tok = mini_dict['start']-len_tok_minus
        end_tok = mini_dict['end']-len_tok_minus
        if start_tok<0:
            print(mini_dict['text'])
        cluster_dict[cluster_no].append({'name': mini_dict['text'],
                                        'pos': [start_tok,end_tok],
                                        'sent_id': mini_dict['sent_id'],
                                        'type': ent_type})
    #Create vertexset
    vertex_set_list = []
    clus_no_to_index = {}
    for j,key in enumerate(sorted(cluster_dict.keys())):
        clus_no_to_index[key] = j
        vertex_set_list.append(cluster_dict[key])
    
    #create labels (problem: labels inconsistent)
    rel_list = []
    for mini_rel_dict in rel_data:
        rel_dict = {}
        r = mini_rel_dict['p']
        h = mini_rel_dict['s']
        t = mini_rel_dict['o']
        try:
            rel_dict['r'] = r
            rel_dict['h'] = clus_no_to_index[h]
            rel_dict['t'] = clus_no_to_index[t]
            rel_dict['evidence'] = [0]
        except:
            continue
        rel_list.append(rel_dict)
    

    
    doc_dict = {}
    doc_dict['vertexSet'] = vertex_set_list
    doc_dict['labels'] = rel_list
    doc_dict['title'] = title
    doc_dict['sents'] = sent_list
    if doc_dict['vertexSet']==[]:
        continue
    if doc_dict['labels']==[]:
        continue
    full_list.append(doc_dict)

test_output = full_list
with open('../data/datasets/dwie_before_preproc/test_joint.json', 'w') as outfile:
    json.dump(test_output, outfile)

In [85]:
dwie_train[0][i]['doc_id']

'train701'

In [87]:
dwie_train[0][i].keys()

dict_keys(['doc_id', 'ner', 'sentences', 'words', 'sections', 'coref', 'n_ary_relations', 'method_subrelations'])

In [86]:
dwie_train[0][i]['sentences']

[[0, 20], [20, 39], [39, 40]]

In [83]:
doc_dict

{'vertexSet': [[{'name': 'Barcelona',
    'pos': [6, 7],
    'sent_id': 0,
    'type': 'location'},
   {'name': 'Barcelona', 'pos': [8, 9], 'sent_id': 0, 'type': 'location'}],
  [{'name': 'Europe', 'pos': [18, 19], 'sent_id': 0, 'type': 'regio'}]],
 'labels': []}

In [80]:
vertex_set_list[20]

[{'name': 'Rashid Bade',
  'pos': [186, 188],
  'sent_id': 9,
  'type': 'politics_per'}]

In [81]:
vertex_set_list[3]

[{'name': 'Tanzania', 'pos': [0, 1], 'sent_id': 0, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [19, 20], 'sent_id': 1, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [65, 66], 'sent_id': 5, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [82, 83], 'sent_id': 5, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [445, 446], 'sent_id': 23, 'type': 'location'}]

In [39]:
full_list

[{'vertexSet': [[{'name': 'Tanzania',
     'pos': [0, 1],
     'sent_id': 0,
     'type': 'location'},
    {'name': 'Tanzania', 'pos': [19, 20], 'sent_id': 1, 'type': 'location'},
    {'name': 'Tanzania', 'pos': [65, 66], 'sent_id': 5, 'type': 'location'},
    {'name': 'Tanzania', 'pos': [82, 83], 'sent_id': 5, 'type': 'location'},
    {'name': 'Tanzania',
     'pos': [445, 446],
     'sent_id': 23,
     'type': 'location'}],
   [{'name': 'Magufuli', 'pos': [2, 3], 'sent_id': 0, 'type': 'politician'},
    {'name': 'John Magufuli',
     'pos': [35, 37],
     'sent_id': 2,
     'type': 'politician'},
    {'name': 'the bulldozer',
     'pos': [56, 58],
     'sent_id': 5,
     'type': 'politician'},
    {'name': 'John Pombe Magufuli',
     'pos': [68, 71],
     'sent_id': 5,
     'type': 'politician'},
    {'name': 'Magufuli',
     'pos': [149, 150],
     'sent_id': 8,
     'type': 'politician'},
    {'name': 'Magufuli',
     'pos': [228, 229],
     'sent_id': 11,
     'type': 'politician'

In [17]:
new_dwie[0][0].keys()

dict_keys(['doc_id', 'ner', 'sentences', 'words', 'sections', 'coref', 'n_ary_relations', 'method_subrelations'])

In [72]:
new_dwie['dataset']['train'][0]['entities'][6]

{'text': 'the bulldozer', 'start': 56, 'end': 58, 'cluster': 2, 'sent_id': 5}

In [75]:
new_dwie['dataset']['train'][0]['entities'][26]

{'text': '$40 million', 'start': 216, 'end': 219, 'cluster': 24, 'sent_id': 10}

In [55]:
cluster_dict[2]

[{'name': 'Magufuli', 'pos': [2, 3], 'sent_id': 0, 'type': 'politician'},
 {'name': 'John Magufuli',
  'pos': [35, 37],
  'sent_id': 2,
  'type': 'politician'},
 {'name': 'the bulldozer',
  'pos': [56, 58],
  'sent_id': 5,
  'type': 'politician'},
 {'name': 'John Pombe Magufuli',
  'pos': [68, 71],
  'sent_id': 5,
  'type': 'politician'},
 {'name': 'Magufuli', 'pos': [149, 150], 'sent_id': 8, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [228, 229], 'sent_id': 11, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [263, 264], 'sent_id': 12, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [306, 307], 'sent_id': 15, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [382, 383], 'sent_id': 20, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [434, 435], 'sent_id': 23, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [471, 472], 'sent_id': 25, 'type': 'politician'},
 {'name': 'Magufuli', 'pos': [474, 475], 'sent_id': 26, 'type': 'politician'},
 {'name': 'Magufuli', 'pos':

In [54]:
cluster_dict[3]

[{'name': 'Tanzania', 'pos': [0, 1], 'sent_id': 0, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [19, 20], 'sent_id': 1, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [65, 66], 'sent_id': 5, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [82, 83], 'sent_id': 5, 'type': 'location'},
 {'name': 'Tanzania', 'pos': [445, 446], 'sent_id': 23, 'type': 'location'}]

In [59]:
new_dwie['dataset']['train'][i]['relations']

[{'s': 1, 'p': 'citizen_of', 'o': 27},
 {'s': 1, 'p': 'citizen_of-x', 'o': 31},
 {'s': 2, 'p': 'agent_of', 'o': 3},
 {'s': 2, 'p': 'citizen_of', 'o': 3},
 {'s': 2, 'p': 'citizen_of-x', 'o': 38},
 {'s': 2, 'p': 'head_of_state', 'o': 3},
 {'s': 2, 'p': 'head_of_state-x', 'o': 38},
 {'s': 4, 'p': 'citizen_of', 'o': 3},
 {'s': 4, 'p': 'citizen_of-x', 'o': 38},
 {'s': 5, 'p': 'citizen_of', 'o': 3},
 {'s': 5, 'p': 'citizen_of-x', 'o': 38},
 {'s': 6, 'p': 'agent_of', 'o': 27},
 {'s': 6, 'p': 'citizen_of', 'o': 27},
 {'s': 6, 'p': 'citizen_of-x', 'o': 31},
 {'s': 6, 'p': 'head_of_state', 'o': 27},
 {'s': 6, 'p': 'head_of_state-x', 'o': 31},
 {'s': 7, 'p': 'agency_of', 'o': 3},
 {'s': 7, 'p': 'agency_of-x', 'o': 38},
 {'s': 7, 'p': 'based_in0', 'o': 3},
 {'s': 7, 'p': 'based_in0-x', 'o': 38},
 {'s': 9, 'p': 'in0', 'o': 42},
 {'s': 19, 'p': 'agency_of', 'o': 3},
 {'s': 19, 'p': 'agency_of-x', 'o': 38},
 {'s': 19, 'p': 'based_in0', 'o': 3},
 {'s': 19, 'p': 'based_in0-x', 'o': 38},
 {'s': 21, 'p':